In [73]:
import geopandas as gpd
import pandas as pd
from pathlib import Path
import json

config = json.load((Path.cwd().parent / 'config.json').open('rb'))
network_fp = Path(config['project_directory']) / "Network"
osmdwnld_fp = Path(config['project_directory']) / "OSM_Download"
elevation_fp = Path(config['project_directory']) / "Elevation"
cyclinginfra_fp = Path(config['project_directory']) / "Cycling_Infra_Dating"
calibration_fp = Path(config['project_directory']) / "Calibration"


In [74]:
import requests

state_two_letter = "ga"
YYYY = 2010

lodes_url_base = f"https://lehd.ces.census.gov/data/lodes/LODES7/{state_two_letter}/od/{state_two_letter}_od_main_JT00_{YYYY}.csv.gz"

In [75]:
import pandas as pd
test = pd.read_csv(lodes_url_base)


In [77]:
rename_dict = {
    'w_geocode':'Work Block ID',
    'h_geocode':'Home Block ID',
    'S000': 'Total Jobs'  
}
test.rename(columns=rename_dict, inplace=True)
test = test[['Work Block ID','Home Block ID','Total Jobs']]

In [78]:
import geopandas as gpd
studyarea = gpd.read_file("/Users/tannerpassmore/Documents/BikewaySim/RAW/SAGIS/savannah_metro.geojson")#.to_crs(config['projected_crs_epsg'])
studyarea = studyarea.unary_union.envelope

In [79]:
blocks = gpd.read_file("/Users/tannerpassmore/Documents/BikewaySim/Savannah/OD Creation/tl_2010_13_tabblock10.shp",mask=studyarea).to_crs(config['projected_crs_epsg'])

In [82]:
#turn to int
test['Work Block ID'] = test['Work Block ID'].astype(int)
test['Home Block ID'] = test['Home Block ID'].astype(int)
blocks['GEOID10'] = blocks['GEOID10'].astype(int)

/var/folders/66/68r0k8s534v4gf9flsfnxnsr0000gn/T/ipykernel_25189/1276318133.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test['Work Block ID'] = test['Work Block ID'].astype(int)
/var/folders/66/68r0k8s534v4gf9flsfnxnsr0000gn/T/ipykernel_25189/1276318133.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test['Home Block ID'] = test['Home Block ID'].astype(int)


In [131]:
works = test[['Work Block ID','Total Jobs']].copy()
works = works.groupby('Work Block ID')['Total Jobs'].sum().reset_index()
works = pd.merge(works,blocks[['GEOID10','geometry']],left_on="Work Block ID",right_on='GEOID10')
works = gpd.GeoDataFrame(works,geometry='geometry')

In [134]:
works.explore('Total Jobs')

In [84]:
merged = pd.merge(test,blocks[['GEOID10','geometry']],left_on="Work Block ID",right_on='GEOID10',how='left')
merged.drop(columns=['GEOID10'],inplace=True)
merged.rename(columns={'geometry':'work_geo'},inplace=True)
merged = pd.merge(merged,blocks[['GEOID10','geometry']],left_on="Home Block ID",right_on='GEOID10',how='left')
merged.drop(columns=['GEOID10'],inplace=True)
merged.rename(columns={'geometry':'home_geo'},inplace=True)
merged = merged[merged['home_geo'].notna() & merged['work_geo'].notna()]

Work Block ID  Total Jobs
0     130299203011024          43
1     130299203011025           2
2     130299203011027           8
3     130299203011028          77
4     130299203011032           1
...               ...         ...
2100  131790105012143          26
2101  131790105012159           1
2102  131790105012161           6
2103  131790105012172          22
2104  131790106002047           7

[2105 rows x 2 columns]

In [118]:
random_id = merged['Work Block ID'].sample(1).item()
subset = merged.loc[merged['Work Block ID']==random_id].copy()
subset = gpd.GeoDataFrame(subset,geometry='home_geo')
m = subset.explore()

In [116]:
blocks.loc[blocks['GEOID10']==random_id,'geometry'].explore()

In [105]:
work = blocks.loc[blocks['GEOID10']==random_id,'geometry'].to_crs('epsg:4326').item().centroid

In [109]:
x, y = list(work.coords)[0]

In [126]:
import folium
folium.Circle((y,x),radius=100,tooltip='WORK',kwargs={'color':'green'}).add_to(m)
m

In [41]:
merged['work_geo'] = gpd.GeoSeries(merged['work_geo']).centroid
merged['home_geo'] = gpd.GeoSeries(merged['home_geo']).centroid

/var/folders/66/68r0k8s534v4gf9flsfnxnsr0000gn/T/ipykernel_25189/3296889057.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  merged['work_geo'] = gpd.GeoSeries(merged['work_geo']).centroid
/var/folders/66/68r0k8s534v4gf9flsfnxnsr0000gn/T/ipykernel_25189/3296889057.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  merged['home_geo'] = gpd.GeoSeries(merged['home_geo']).centroid


In [ ]:
# import geopandas as gpd
# import pandas as pd
# from pathlib import Path
# import json

# config = json.load((Path.cwd().parent / 'config.json').open('rb'))
# network_fp = Path(config['project_directory']) / "Network"
# osmdwnld_fp = Path(config['project_directory']) / "OSM_Download"
# elevation_fp = Path(config['project_directory']) / "Elevation"
# cyclinginfra_fp = Path(config['project_directory']) / "Cycling_Infra_Dating"
# calibration_fp = Path(config['project_directory']) / "Calibration"

In [147]:



#'foot' in blocks.crs.axis_info[0].unit_name

#df.crs.axis_info[0].unit_name

True